In [54]:
from minio import Minio
import duckdb
import pandas as pd

In [55]:
# add the access key cell here


In [56]:
bucket_name = "ads-with-images"
object_name = "aug_ads_w_images.parquet"

df = connection.execute(f"SELECT * FROM parquet_scan('s3://{bucket_name}/{object_name}');").df()
df = df.iloc[:1000]

In [57]:
df.head()

url  \
0  https://www.ebay.ie/itm/225712575933?amdata=en...   
1  https://www.ebay.nl/itm/165510736761?amdata=en...   
2  https://www.ebay.nl/itm/175641098586?amdata=en...   
3  https://www.ebay.com.hk/itm/256119308608?amdat...   
4  https://www.ebay.at/itm/134672898114?amdata=en...   

                                               title  \
0  Mofusand Exhibition Mofusando Piece Set Towel ...   
1  ATLANTIC RIGHT WHALE =Endangered= IDENTICAL St...   
2  Mountain Anoa Dwarf Water Buffalo DecoBronze S...   
3  Wildlife Research Center 1255 Scent Killer Gol...   
4  4 "Sammeln Sie rote Kupferschnitzerei Manis pe...   

                                                text       domain  \
0  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\nMofusa...      ebay.ie   
1  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\nATLANT...      ebay.nl   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\nMounta...      ebay.nl   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\nWildli...  ebay.com.hk   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n4 "Sam...      ebay.at   

                                                name  \
0  Mofusand Exhibition Mofusando Piece Set Towel ...   
1  ATLANTIC RIGHT WHALE =Endangered= IDENTICAL St...   
2  Mountain Anoa Dwarf Water Buffalo DecoBronze S...   
3  Wildlife Research Center 1255 Scent Killer Gol...   
4  4 "Sammeln Sie rote Kupferschnitzerei Manis pe...   

                                         description  \
0  Mofusand Exhibition Mofusando Piece Set Towel ...   
1  ATLANTIC RIGHT WHALE =Endangered= IDENTICAL St...   
2  Mountain Anoa Dwarf Water Buffalo DecoBronze S...   
3  Wildlife Research Center 1255 Scent Killer Gol...   
4  4 "Sammeln Sie rote Kupferschnitzerei Manis pe...   

                                               image  \
0  https://i.ebayimg.com/images/g/CUQAAOSwatNkz~R...   
1  https://i.ebayimg.com/images/g/m8cAAOSwfbNillr...   
2  https://i.ebayimg.com/images/g/VAMAAOSwxNlkBe4...   
3  https://i.ebayimg.com/images/g/w3IAAOSwUp9jOv-...   
4  https://i.ebayimg.com/images/g/c3YAAOSwM9NiNFP...   

                      retrieved production_data category  ...  loc_name lat  \
0  2023-02-10T17:05:03.245+0000            None     None  ...      None NaN   
1  2023-02-10T17:05:03.245+0000            None     None  ...      None NaN   
2  2023-02-10T17:05:03.245+0000            None     None  ...      None NaN   
3  2023-02-10T17:05:03.245+0000            None     None  ...      None NaN   
4  2023-02-10T17:05:03.245+0000            None     None  ...      None NaN   

  lon country label     score  \
0 NaN    None   0.0  0.990042   
1 NaN    None   1.0  0.977253   
2 NaN    None   0.0  0.819862   
3 NaN    None   1.0  0.815647   
4 NaN    None   1.0  0.734359   

                                             product         label_product  \
0  Mofusand Exhibition Mofusando Piece Set Towel ...             an object   
1  ATLANTIC RIGHT WHALE =Endangered= IDENTICAL St...             an object   
2  Mountain Anoa Dwarf Water Buffalo DecoBronze S...  a print of an animal   
3  Wildlife Research Center 1255 Scent Killer Gol...             an object   
4  4 "Sammeln Sie rote Kupferschnitzerei Manis pe...  a print of an animal   

  score_product                                               path  
0      0.454573  images-august/None/e8bf594b-d5bb-43b5-a1b1-18f...  
1      0.728779  images-august/None/286b368a-8adf-46ce-9331-e29...  
2      0.504843  images-august/None/07c9d7ab-0264-44e5-8c1d-934...  
3      0.738707  images-august/None/871b28ed-2e92-4c3d-8e1d-2b9...  
4      0.538278  images-august/None/7bfee649-2c7c-46b9-b5b4-37e...  

[5 rows x 28 columns]

In [58]:
from torch.utils.data import DataLoader, Dataset, random_split
from transformers import BertTokenizer, BertForSequenceClassification, AdamW
from torchvision.transforms import transforms
import torch.nn as nn
import torch
from transformers import BertModel, RobertaModel
from torchvision.models import resnet50
from torch import cuda
from PIL import Image
import time
from transformers import RobertaForSequenceClassification, RobertaTokenizer
from torchvision import models
import torch.nn.functional as F

In [59]:
from io import BytesIO

In [60]:
# We will first prepare the dataset for inference
class InferenceDataset(Dataset):
    def __init__(self, dataframe, tokenizer, max_len, transform=None):
        self.dataframe = dataframe
        self.tokenizer = tokenizer
        self.max_len = max_len
        self.transform = transform
    
    def __len__(self):
        return len(self.dataframe)

    def __getitem__(self, idx):
        row = self.dataframe.iloc[idx]
        text = row['combined_text']
        img_path = row['path']
        
        # Processing text
        encoding = self.tokenizer.encode_plus(
            text,
            add_special_tokens=True,
            max_length=self.max_len,
            return_token_type_ids=False,
            padding='max_length',
            return_attention_mask=True,
            return_tensors='pt',
            truncation=True
        )
        
        bucket_name, _, object_name = img_path.partition('/')
        image_data = client.get_object(bucket_name, object_name)
        image_bytes = image_data.read()
        image = Image.open(BytesIO(image_bytes)).convert("RGB")
        
        # Processing images
        # image = Image.open(img_path).convert("RGB")
        if self.transform:
            image = self.transform(image)
        
        return {
            'input_ids': encoding['input_ids'].flatten(),
            'attention_mask': encoding['attention_mask'].flatten(),
            'image': image
        }


In [61]:
# Constants
MAX_LEN = 128
BATCH_SIZE = 16

tokenizer = RobertaTokenizer.from_pretrained('roberta-base')

transform = transforms.Compose([
    transforms.RandomHorizontalFlip(),
    transforms.RandomRotation(10),
    transforms.RandomResizedCrop(224, scale=(0.8, 1.0)),
    transforms.ColorJitter(brightness=0.2, contrast=0.2, saturation=0.2, hue=0.1),
    transforms.ToTensor(),
])


# Combine text fields
df['description'] = df['description'].fillna('')
df['combined_text'] = df['title'] + ' ' + df['text'] + ' ' + df['description']

# Prepare dataset and dataloader for inference
inference_dataset = InferenceDataset(
    dataframe=df,
    tokenizer=tokenizer,  
    max_len=MAX_LEN,
    transform=transform
)

inference_dataloader = DataLoader(inference_dataset, batch_size=BATCH_SIZE, shuffle=False)

In [62]:
text = RobertaModel.from_pretrained('roberta-base')

img = models.swin_v2_b(pretrained=True)

class MultiHeadCrossAttention(nn.Module):
    def __init__(self, text_dim, image_dim, num_heads, hidden_dim, output_dim):
        super(MultiHeadCrossAttention, self).__init__()
        self.num_heads = num_heads
        self.head_dim = hidden_dim // num_heads

        # These linear layers project the inputs to multiple heads
        self.text_query = nn.Linear(text_dim, hidden_dim, bias=False)
        self.text_key = nn.Linear(text_dim, hidden_dim, bias=False)
        self.text_value = nn.Linear(text_dim, hidden_dim, bias=False)

        self.image_query = nn.Linear(image_dim, hidden_dim, bias=False)
        self.image_key = nn.Linear(image_dim, hidden_dim, bias=False)
        self.image_value = nn.Linear(image_dim, hidden_dim, bias=False)

        # Final projection layer
        self.out_proj = nn.Linear(hidden_dim, output_dim, bias=False)

    def forward(self, text_features, image_features):
        Q_text = self.text_query(text_features)
        K_text = self.text_key(text_features)
        V_text = self.text_value(text_features)

        Q_image = self.image_query(image_features)
        K_image = self.image_key(image_features)
        V_image = self.image_value(image_features)

        # Split the hidden dimension into num_heads
        Q_text = Q_text.view(Q_text.size(0), -1, self.num_heads, self.head_dim).transpose(1, 2)
        K_text = K_text.view(K_text.size(0), -1, self.num_heads, self.head_dim).transpose(1, 2)
        V_text = V_text.view(V_text.size(0), -1, self.num_heads, self.head_dim).transpose(1, 2)

        Q_image = Q_image.view(Q_image.size(0), -1, self.num_heads, self.head_dim).transpose(1, 2)
        K_image = K_image.view(K_image.size(0), -1, self.num_heads, self.head_dim).transpose(1, 2)
        V_image = V_image.view(V_image.size(0), -1, self.num_heads, self.head_dim).transpose(1, 2)

        # Calculate the attention scores
        attn_scores_text_image = torch.matmul(Q_text, K_image.transpose(-1, -2)) / (self.head_dim ** 0.5)
        attn_scores_image_text = torch.matmul(Q_image, K_text.transpose(-1, -2)) / (self.head_dim ** 0.5)

        # Normalize scores
        attn_probs_text_image = F.softmax(attn_scores_text_image, dim=-1)
        attn_probs_image_text = F.softmax(attn_scores_image_text, dim=-1)

        # Apply attention
        attn_output_text_image = torch.matmul(attn_probs_text_image, V_image)
        attn_output_image_text = torch.matmul(attn_probs_image_text, V_text)

        # Concatenate the results across the heads
        attn_output_text_image = attn_output_text_image.transpose(1, 2).contiguous().view(text_features.size(0), -1)
        attn_output_image_text = attn_output_image_text.transpose(1, 2).contiguous().view(image_features.size(0), -1)

        # Project to output dimension
        output_text_image = self.out_proj(attn_output_text_image)
        output_image_text = self.out_proj(attn_output_image_text)

        return output_text_image, output_image_text


class MultiModalModel(nn.Module):
            def __init__(self, num_labels):
                super(MultiModalModel, self).__init__()

                # Load pre-trained models
                self.bert = text
                self.resnet = img

                # Remove the final classification layer of ResNet
                self.resnet = nn.Sequential(*list(self.resnet.children())[:-1])
                self.mhca = MultiHeadCrossAttention(text_dim=768, image_dim=1024, num_heads=4, hidden_dim=512, output_dim=2048)
                
                
                self.classifier = nn.Sequential(
                    nn.Linear(2816, 512), 
                    nn.ReLU(),
                    nn.Dropout(0.2),
                    nn.Linear(512, num_labels)
                )

            def forward(self, input_ids, attention_mask, image):
                # Forward pass through BERT
                outputs = self.bert(input_ids=input_ids, attention_mask=attention_mask)
                text_features = outputs['last_hidden_state'][:, 0, :]  # CLS token output as text feature
                
                # Forward pass through ResNet
                image_features = self.resnet(image)
                image_features = image_features.view(image_features.size(0), -1)  # Flatten the output
                
                if text_features.dim() == 2:
                    text_features = text_features.unsqueeze(1)
                if image_features.dim() == 2:
                    image_features = image_features.unsqueeze(1)
                
                attended_text, attended_image = self.mhca(text_features, image_features)
                
                attended_text = attended_text.squeeze(1)  # shape: [16, 768]
                attended_image = attended_image.squeeze(1) # shape: [16, 2048]

                self.image_projection = torch.nn.Linear(2048, 768).to(device)
                attended_image = self.image_projection(attended_image)
                combined_features = torch.cat((attended_text, attended_image), dim=-1)

                logits = self.classifier(combined_features)

                return logits



Some weights of RobertaModel were not initialized from the model checkpoint at roberta-base and are newly initialized: ['roberta.pooler.dense.bias', 'roberta.pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/home/jovyan/.local/lib/python3.9/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/home/jovyan/.local/lib/python3.9/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=Swin_V2_B_Weights.IMAGENET1K_V1`. You can also use `weights=Swin_V2_B_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)


In [63]:
        import urllib3, socket
        from urllib3.connection import HTTPConnection
    
        HTTPConnection.default_socket_options = ( 
            HTTPConnection.default_socket_options + [
            (socket.SOL_SOCKET, socket.SO_SNDBUF, 1000000), #1MB in byte
            (socket.SOL_SOCKET, socket.SO_RCVBUF, 1000000)
        ])

In [64]:
# Function to run inference
def run_inference(model, dataloader, device):
    model.eval()
    predictions = []

    with torch.no_grad():
        for batch in dataloader:
            input_ids = batch['input_ids'].to(device)
            attention_mask = batch['attention_mask'].to(device)
            images = batch['image'].to(device)
            
            outputs = model(input_ids=input_ids, attention_mask=attention_mask, image=images)
            
            preds = torch.argmax(outputs, dim=1)
            predictions.extend(preds.cpu().numpy())
    
    return predictions


In [ ]:
# Initialize an empty model
loaded_model = MultiModalModel(num_labels=2)

# Load the state dictionary
model_load_path = "./model.pth"

# Check device
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

# Load the model weights
if device == torch.device('cpu'):
    loaded_model.load_state_dict(torch.load(model_load_path, map_location=device), strict=False)
else:
    loaded_model.load_state_dict(torch.load(model_load_path), strict=False)

# Move model to evaluation mode and to the device
loaded_model.eval()
loaded_model = loaded_model.to(device)

start_time = time.time()

# Get the predictions
predictions = run_inference(loaded_model, inference_dataloader, device)

end_time = time.time()

elapsed_time = end_time - start_time
print(f"Inference took {elapsed_time:.2f} seconds")


# Add predictions to the dataframe
df['predicted_label'] = predictions

In [ ]:
df.head()